### Import Lib

In [26]:
import geopandas as gpd
import pandas as pd
import numpy as np
from shapely.wkt import loads
import constant as c
from pyproj import CRS
import sys;sys.path.append('../')
from itertools import combinations
from sklearn.preprocessing import StandardScaler
import math
import matplotlib.pyplot as plt
import warnings; warnings.filterwarnings('ignore')

### Acquire Data

In [27]:
# then read the data
df_2020 = pd.read_csv('../asset/preprocess/df_2020.csv', index_col=0)
df_2020['geometry_grids'] = df_2020['geometry_grids'].apply(lambda x: loads(x))
df_2021 = pd.read_csv('../asset/preprocess/df_2021.csv', index_col=0)
df_2021['geometry_grids'] = df_2021['geometry_grids'].apply(lambda x: loads(x))
df_2022 = pd.read_csv('../asset/preprocess/df_2022.csv', index_col=0)
df_2022['geometry_grids'] = df_2022['geometry_grids'].apply(lambda x: loads(x))

crs = 'EPSG:5179'  # Specify the coordinate reference system
gdf_2020 = gpd.GeoDataFrame(df_2020, geometry=df_2020['geometry_grids'], crs=crs)
gdf_2021 = gpd.GeoDataFrame(df_2021, geometry=df_2021['geometry_grids'], crs=crs)
gdf_2022 = gpd.GeoDataFrame(df_2022, geometry=df_2022['geometry_grids'], crs=crs)

gdf_2020_scbd = gdf_2020[gdf_2020['sigungunm'].isin(c.SCBD_NMS)]
gdf_2020_gbd = gdf_2020[gdf_2020['sigungunm'].isin(c.GBD_NMS)]
gdf_2020_ybd = gdf_2020[gdf_2020['sigungunm'].isin(c.YBD_NMS)]
gdf_2021_scbd = gdf_2021[gdf_2021['sigungunm'].isin(c.SCBD_NMS)]
gdf_2021_gbd = gdf_2021[gdf_2021['sigungunm'].isin(c.GBD_NMS)]
gdf_2021_ybd = gdf_2021[gdf_2021['sigungunm'].isin(c.YBD_NMS)]
gdf_2022_scbd = gdf_2022[gdf_2022['sigungunm'].isin(c.SCBD_NMS)]
gdf_2022_gbd = gdf_2022[gdf_2022['sigungunm'].isin(c.GBD_NMS)]
gdf_2022_ybd = gdf_2022[gdf_2022['sigungunm'].isin(c.YBD_NMS)]

In [28]:
# Setting COLS
SIM_CAL_COLS = c.SIM_CAL_COLS
STANDARDIZE_COLS = c.STANDARDIZE_COLS
PP_COLS = c.PP_COLS
BS_COLS = c.BS_COLS
BD_COLS = c.BD_COLS

### Experiment Settings

In [74]:
# experiment settings
YEAR = 2021
CBD_NM = "ybd"

In [76]:
# Construct the DataFrame variable name
df_nm = f'gdf_{YEAR}_{CBD_NM}'
gdf = gpd.GeoDataFrame(locals()[df_nm], geometry='geometry_grids')
MAX_GRIDS_N = int(len(gdf) * 0.1)
print(f"Total Grids: {len(gdf)}\nNum Max grids: {MAX_GRIDS_N}")

# Set the CRS for the GeoDataFrame
crs = CRS.from_epsg(5179)
gdf = gdf.set_crs(crs)
gdf = gdf.dropna() # drop any data have null value

# and normailze
# Initialize the StandardScaler object
scaler = StandardScaler()
# Fit the scaler to the data
scaler.fit(gdf[STANDARDIZE_COLS])
# Transform the data using the scaler
normalized_data = scaler.transform(gdf[STANDARDIZE_COLS])
gdf_normalized = gdf.copy()
gdf_normalized[STANDARDIZE_COLS] = normalized_data

Total Grids: 647
Num Max grids: 64


In [78]:
# First, get the result data(phase_results)
result_fpath = f"../asset/experiment/cluster/{CBD_NM}_{YEAR}.csv"
phase_results = pd.read_csv(result_fpath)[['grid_idx', 'phase']]
phase_results['grid_idx'] = phase_results['grid_idx'].astype(int)
phase_results['phase'] = phase_results['phase'].astype(int)
cluster_idxs = list(phase_results.grid_idx)

gdf_ours = gdf_normalized.copy()
gdf_ours['cluster'] = np.where(gdf_ours['grid_idx'].isin(cluster_idxs), 1, 0)
gdf_ours

grid_idx    pp_pop     pp_od    pp_drr   bs_ebit  \
0       10718 -0.995220 -0.491446 -1.178617 -0.514178   
1       10719 -1.169829 -0.513928 -0.696546 -0.514147   
2       10739 -1.336759 -0.484143 -1.178617 -0.515097   
3       10745 -0.474751 -0.521953 -0.138827 -0.490437   
4       10764 -1.278122 -0.270151 -0.646188 -0.514940   
..        ...       ...       ...       ...       ...   
642     12650 -0.441089 -0.741307  0.840866  1.610821   
643     12677 -0.659415 -0.811485  0.979739  1.727677   
644     12702 -0.426071 -0.811241 -0.188835  1.457449   
645     12778 -1.196816 -1.423362 -0.464470  1.435335   
646     12800 -1.204029 -1.430411 -0.531921  1.305197   

                                        geometry_grids sigungunm  \
0    POLYGON ((945535.230 1946565.548, 945535.230 1...      영등포구   
1    POLYGON ((945535.230 1946665.548, 945535.230 1...      영등포구   
2    POLYGON ((945635.230 1946365.548, 945635.230 1...      영등포구   
3    POLYGON ((945635.230 1946965.548, 945635.230 1...      영등포구   
4    POLYGON ((945735.230 1946265.548, 945735.230 1...      영등포구   
..                                                 ...       ...   
642  POLYGON ((949835.230 1946565.548, 949835.230 1...      영등포구   
643  POLYGON ((949935.230 1946665.548, 949935.230 1...      영등포구   
644  POLYGON ((950035.230 1946565.548, 950035.230 1...      영등포구   
645  POLYGON ((950335.230 1946765.548, 950335.230 1...      영등포구   
646  POLYGON ((950435.230 1946765.548, 950435.230 1...      영등포구   

                      platplc           x          y  ...  bd_totflrcnt  \
0     서울특별시 영등포구 문래동5가 23-5번지  126.883851  37.517448  ...      0.183410   
1     서울특별시 영등포구 문래동5가 23-2번지  126.883935  37.517784  ...     -0.828574   
2    서울특별시 영등포구 문래동5가 20-20번지  126.885534  37.515291  ...      2.110999   
3     서울특별시 영등포구 문래동6가 34-1번지  126.885623  37.520634  ...     -0.298487   
4      서울특별시 영등포구 문래동5가 5-4번지  126.886766  37.514684  ...     -0.924954   
..                        ...         ...        ...  ...           ...   
642    서울특별시 영등포구 여의도동 54-7번지  126.932886  37.517758  ...     -0.732195   
643    서울특별시 영등포구 여의도동 53-3번지  126.933547  37.518740  ...     -0.635816   
644      서울특별시 영등포구 여의도동 62번지  126.935605  37.517823  ...     -0.587626   
645    서울특별시 영등포구 여의도동 61-4번지  126.939026  37.518953  ...      0.376169   
646      서울특별시 영등포구 여의도동 60번지  126.939838  37.519576  ...      2.014619   

     bd_elvtent    bs_gas   bs_elct  bd_height    bd_ilp  bd_vintage  count  \
0      0.009522  0.282356 -0.130366   1.135105 -0.613023   -0.169425    4.0   
1     -0.094195 -0.328155 -0.342241  -0.521360 -0.600318   -1.270418    4.0   
2     -0.163339  0.184416 -0.241635  -0.274552 -0.634695   -0.792209    4.0   
3     -0.094195 -0.036427 -0.243141   0.625351 -0.438710   -1.570688    4.0   
4     -0.301628 -0.328155 -0.342241  -0.578316 -0.538114    0.030755    3.0   
..          ...       ...       ...        ...       ...         ...    ...   
642   -0.301628 -0.274568 -0.330360  -0.517563  1.435533    2.733191    5.0   
643   -0.094195 -0.328155 -0.238374  -0.077105  1.260712    1.832379    5.0   
644   -0.197911  4.871587  2.798829   0.395249  1.192613   -1.020192    5.0   
645    0.735538 -0.015357  0.353798   2.314281  1.772978    0.831477    9.0   
646    6.958529  6.047239  6.572019   8.442728  2.445835    1.632199    9.0   

                                              geometry  cluster  
0    POLYGON ((945535.230 1946565.548, 945535.230 1...        0  
1    POLYGON ((945535.230 1946665.548, 945535.230 1...        0  
2    POLYGON ((945635.230 1946365.548, 945635.230 1...        0  
3    POLYGON ((945635.230 1946965.548, 945635.230 1...        0  
4    POLYGON ((945735.230 1946265.548, 945735.230 1...        0  
..                                                 ...      ...  
642  POLYGON ((949835.230 1946565.548, 949835.230 1...        1  
643  POLYGON ((949935.230 1946665.548, 949935.230 1...        1  
644  POLYGON ((950035.230 1946565.548, 950035.230 1...     

In [ ]:
cluster_idxs = list(phase_results.grid_idx)
merged_gdf = gpd.GeoDataFrame(gdf_normalized.merge(phase_results[['grid_idx', 'phase']], on='grid_idx', how='left'))
cluster_gdf = merged_gdf[merged_gdf['grid_idx'].isin(cluster_idxs)]
cluster_gdf.explore(column = 'phase', cmap = 'Blues')

Total Grids: 647
Num Max grids: 64


In [57]:
gdf_normalized[['geometry_grids', 'bdnm']].explore(cmap = 'Blues')

In [62]:
import numpy as np
from sklearn.cluster import DBSCAN
from sklearn import metrics
from geopy.distance import great_circle
from shapely.geometry import MultiPoint

# Select the data
coords = gdf_normalized[['x', 'y']].values

# Define the DBSCAN model
# In this example, eps is set to 0.5 and min_samples is set to 5.
# You can adjust these values as necessary to optimize the performance of your model.
# The value for eps should be chosen based on the data and distance metric, and it may take some trial and error to find a value that performs well for your data.
kms_per_radian = 6371.0088
epsilon = 1.5 / kms_per_radian # 1.5 was chosen arbitrarily here
db = DBSCAN(eps=epsilon, min_samples=30, algorithm='ball_tree', metric='haversine').fit(np.radians(coords))

# Create a new column in your geodataframe with the labels from DBSCAN
gdf_normalized['cluster'] = db.labels_

# Now you can visualize the results
gdf_normalized.explore(column='cluster', cmap = 'Blues')

In [61]:
gdf_normalized

grid_idx    pp_pop     pp_od    pp_drr   bs_ebit  \
0       10718 -0.995220 -0.491446 -1.178617 -0.514178   
1       10719 -1.169829 -0.513928 -0.696546 -0.514147   
2       10739 -1.336759 -0.484143 -1.178617 -0.515097   
3       10745 -0.474751 -0.521953 -0.138827 -0.490437   
4       10764 -1.278122 -0.270151 -0.646188 -0.514940   
..        ...       ...       ...       ...       ...   
642     12650 -0.441089 -0.741307  0.840866  1.610821   
643     12677 -0.659415 -0.811485  0.979739  1.727677   
644     12702 -0.426071 -0.811241 -0.188835  1.457449   
645     12778 -1.196816 -1.423362 -0.464470  1.435335   
646     12800 -1.204029 -1.430411 -0.531921  1.305197   

                                        geometry_grids sigungunm  \
0    POLYGON ((945535.230 1946565.548, 945535.230 1...      영등포구   
1    POLYGON ((945535.230 1946665.548, 945535.230 1...      영등포구   
2    POLYGON ((945635.230 1946365.548, 945635.230 1...      영등포구   
3    POLYGON ((945635.230 1946965.548, 945635.230 1...      영등포구   
4    POLYGON ((945735.230 1946265.548, 945735.230 1...      영등포구   
..                                                 ...       ...   
642  POLYGON ((949835.230 1946565.548, 949835.230 1...      영등포구   
643  POLYGON ((949935.230 1946665.548, 949935.230 1...      영등포구   
644  POLYGON ((950035.230 1946565.548, 950035.230 1...      영등포구   
645  POLYGON ((950335.230 1946765.548, 950335.230 1...      영등포구   
646  POLYGON ((950435.230 1946765.548, 950435.230 1...      영등포구   

                      platplc           x          y  ...  bd_totflrcnt  \
0     서울특별시 영등포구 문래동5가 23-5번지  126.883851  37.517448  ...      0.183410   
1     서울특별시 영등포구 문래동5가 23-2번지  126.883935  37.517784  ...     -0.828574   
2    서울특별시 영등포구 문래동5가 20-20번지  126.885534  37.515291  ...      2.110999   
3     서울특별시 영등포구 문래동6가 34-1번지  126.885623  37.520634  ...     -0.298487   
4      서울특별시 영등포구 문래동5가 5-4번지  126.886766  37.514684  ...     -0.924954   
..                        ...         ...        ...  ...           ...   
642    서울특별시 영등포구 여의도동 54-7번지  126.932886  37.517758  ...     -0.732195   
643    서울특별시 영등포구 여의도동 53-3번지  126.933547  37.518740  ...     -0.635816   
644      서울특별시 영등포구 여의도동 62번지  126.935605  37.517823  ...     -0.587626   
645    서울특별시 영등포구 여의도동 61-4번지  126.939026  37.518953  ...      0.376169   
646      서울특별시 영등포구 여의도동 60번지  126.939838  37.519576  ...      2.014619   

     bd_elvtent    bs_gas   bs_elct  bd_height    bd_ilp  bd_vintage  count  \
0      0.009522  0.282356 -0.130366   1.135105 -0.613023   -0.169425    4.0   
1     -0.094195 -0.328155 -0.342241  -0.521360 -0.600318   -1.270418    4.0   
2     -0.163339  0.184416 -0.241635  -0.274552 -0.634695   -0.792209    4.0   
3     -0.094195 -0.036427 -0.243141   0.625351 -0.438710   -1.570688    4.0   
4     -0.301628 -0.328155 -0.342241  -0.578316 -0.538114    0.030755    3.0   
..          ...       ...       ...        ...       ...         ...    ...   
642   -0.301628 -0.274568 -0.330360  -0.517563  1.435533    2.733191    5.0   
643   -0.094195 -0.328155 -0.238374  -0.077105  1.260712    1.832379    5.0   
644   -0.197911  4.871587  2.798829   0.395249  1.192613   -1.020192    5.0   
645    0.735538 -0.015357  0.353798   2.314281  1.772978    0.831477    9.0   
646    6.958529  6.047239  6.572019   8.442728  2.445835    1.632199    9.0   

                                              geometry  cluster  
0    POLYGON ((945535.230 1946565.548, 945535.230 1...        0  
1    POLYGON ((945535.230 1946665.548, 945535.230 1...        0  
2    POLYGON ((945635.230 1946365.548, 945635.230 1...        0  
3    POLYGON ((945635.230 1946965.548, 945635.230 1...        0  
4    POLYGON ((945735.230 1946265.548, 945735.230 1...        0  
..                                                 ...      ...  
642  POLYGON ((949835.230 1946565.548, 949835.230 1...        0  
643  POLYGON ((949935.230 1946665.548, 949935.230 1...        0  
644  POLYGON ((950035.230 1946565.548, 950035.230 1...     

In [43]:
from sklearn.cluster import DBSCAN
model = DBSCAN(eps=0.1, min_samples=2)
model.fit(gdf_normalized[SIM_CAL_COLS])
gdf_normalized['cluster'] = model.fit_predict(gdf_normalized[SIM_CAL_COLS])

In [44]:
gdf_normalized.explore(column='cluster', cmap='viridis')

In [67]:
from sklearn.cluster import KMeans
import matplotlib.pyplot as plt
from sklearn.metrics import silhouette_score

# Choose the number of clusters
n_clusters = 2  # for example

# Create a KMeans instance
kmeans = KMeans(n_clusters=n_clusters)

# Fit the model to your data (coordinates)
kmeans.fit(gdf_normalized[SIM_CAL_COLS])

# Create a new column in your geodataframe with the labels from KMeans
gdf_normalized['cluster'] = kmeans.labels_

# Visualize the results
# fig, ax = plt.subplots(figsize=(10,10))  
gdf_normalized.explore(column='cluster', cmap='viridis') 
# plt.show()

In [68]:
silhouette_score(gdf_normalized[SIM_CAL_COLS], kmeans.labels_)

0.5576196770750959

In [24]:
gdf_normalized.explore(column = 'cluster')